In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split

In [2]:
pip install pandas-profiling

     |████████████████████████████████| 243 kB 16.2 MB/s eta 0:00:01
     |████████████████████████████████| 75 kB 7.2 MB/s  eta 0:00:01
     |████████████████████████████████| 74 kB 4.6 MB/s  eta 0:00:01
     |████████████████████████████████| 1.1 MB 56.3 MB/s eta 0:00:01
     |████████████████████████████████| 3.1 MB 68.0 MB/s eta 0:00:01
     |████████████████████████████████| 295 kB 73.0 MB/s eta 0:00:01
  Created wheel for htmlmin: filename=htmlmin-0.1.12-py3-none-any.whl size=27085 sha256=2626e0421d3dee60df182cc6d612bcea2f7d0bc22bdf4e6048e510fe3faf8abc
  Stored in directory: /home/ec2-user/.cache/pip/wheels/c3/fe/0b/4450b38bceb9ae43dd7d0f16e353566f30f5f4d59a58eca2ed
  Created wheel for phik: filename=phik-0.11.2-py3-none-any.whl size=1107412 sha256=63cb90630b84363838eaa5570fda2a1c1f18d4764653b89dacd8eb85fc4d89ee
  Stored in directory: /home/ec2-user/.cache/pip/wheels/f3/07/e7/fa7fe51fbadefed0ef47a4757912d4ace82c2dfb788b8560ef
Successfully built htmlmin phik
Note: you may need to 

In [2]:
import sagemaker
from sagemaker import get_execution_role
import json
import boto3
import nltk

In [3]:
ds = pd.read_csv('hr_train.csv')

In [4]:
ds

last_new_job  target  city_development_index gender  \
0               1       1                   0.920   Male   
1           never       1                   0.789    NaN   
2               1       1                   0.764    NaN   
3              >4       1                   0.762   Male   
4               1       1                   0.920   Male   
...           ...     ...                     ...    ...   
4772            1       1                   0.624   Male   
4773            3       1                   0.624    NaN   
4774            1       1                   0.920   Male   
4775            1       1                   0.878   Male   
4776            4       1                   0.920   Male   

          relevent_experience enrolled_university education_level  \
0     Has relevent experience       no_enrollment        Graduate   
1      No relevent experience                 NaN        Graduate   
2     Has relevent experience    Part time course        Graduate   
3     Has relevent experience       no_enrollment        Graduate   
4     Has relevent experience       no_enrollment        Graduate   
...                       ...                 ...             ...   
4772   No relevent experience    Full time course        Graduate   
4773  Has relevent experience       no_enrollment         Masters   
4774  Has relevent experience       no_enrollment         Masters   
4775   No relevent experience       no_enrollment        Graduate   
4776  Has relevent experience       no_enrollment        Graduate   

     major_discipline experience company_size company_type  training_hours  
0                STEM        >20          NaN          NaN              36  
1     Business Degree         <1          NaN      Pvt Ltd              52  
2                STEM         11          NaN          NaN              24  
3                STEM         13          <10      Pvt Ltd              18  
4                STEM          7        50-99      Pvt Ltd              46  
...               ...        ...          ...          ...             ...  
4772             STEM          1      100-500      Pvt Ltd              52  
4773             STEM          3      100-500      Pvt Ltd              40  
4774             STEM          9        50-99      Pvt Ltd              36  
4775       Humanities         14          NaN          NaN              42  
4776             STEM         14          NaN          NaN              52  

[4777 rows x 12 columns]

In [5]:
ds = ds.dropna()


In [6]:

import pandas_profiling as pp
pp.ProfileReport(ds)

Summarize dataset:   0%|          | 0/26 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [8]:
ds.head()

last_new_job  target  city_development_index gender  \
3            >4       1                   0.762   Male   
4             1       1                   0.920   Male   
10            2       1                   0.624   Male   
11            4       1                   0.926   Male   
13            3       1                   0.624   Male   

        relevent_experience enrolled_university education_level  \
3   Has relevent experience       no_enrollment        Graduate   
4   Has relevent experience       no_enrollment        Graduate   
10  Has relevent experience       no_enrollment        Graduate   
11  Has relevent experience       no_enrollment             Phd   
13  Has relevent experience    Part time course         Masters   

   major_discipline experience company_size    company_type  training_hours  
3              STEM         13          <10         Pvt Ltd              18  
4              STEM          7        50-99         Pvt Ltd              46  
10             STEM         18        50-99  Funded Startup              68  
11             STEM        >20      100-500         Pvt Ltd              42  
13             STEM          9    5000-9999         Pvt Ltd               7

In [9]:
from sklearn.preprocessing import LabelEncoder

# I do this manually to explicitly tell the model that a better education & experience serves well as a trustworthy input.

# However, later we wil see the feature importanes report in SHAP and notice interesting results.
experience_dict = {'Has relevent experience' : 1,
             'No relevent experience': 0}


company_size= {'50-99' : 99,
             '100-500' : 500,
             '10000+' : 10000,
              'Oct-49' : 49,
             '1000-4999' : 4999,
             '<10' : 10,
              '500-999' : 999,
              '5000-9999' : 9999}

last_new_job= {'1' : 1,
             '2' : 2,
             '3' : 3,
             '>4' : 5,
             'never' : 0,
              '4' : 4}

education_dict = {'Graduate' : 0,
             'Masters' : 1,
             'Phd' : 2}

enrollment_dict = {'no_enrollment' : 2,
             'Full time course' : 1,
             'Part time course' : 0}

gender_dict = {'Male' : 2,
             'Female' : 1,
             'Other' : 0}

discipline_dict = {'STEM' : 5,
             'Humanities' : 4,
             'Business Degree' : 3,
             'Other' : 2,
             'No Major' : 1,
             'Arts' : 0 }

company_dict = {'Pvt Ltd' : 5,
             'Funded Startup' : 4,
             'Public Sector' : 3,
             'Early Stage Startup' : 2,
             'NGO' : 1,
             'Other' : 0 }


# Train encoding
le = LabelEncoder()
ds['gender'] = ds['gender'].map(gender_dict)
ds['relevent_experience'] = ds['relevent_experience'].map(experience_dict)
ds['last_new_job'] = ds['last_new_job'].map(last_new_job)
ds['company_size'] = ds['company_size'].map(company_size)
ds['education_level'] = ds['education_level'].map(education_dict)
ds['enrolled_university'] = ds['enrolled_university'].map(enrollment_dict)
ds['major_discipline'] = ds['major_discipline'].map(discipline_dict)
ds['experience'] = le.fit_transform(ds['experience'].astype(str))
# ds['company_size'] = le.fit_transform(ds['company_size'].astype(str))
ds['company_type'] = ds['company_type'].map(company_dict)
# ds['last_new_job'] = le.fit_transform(ds['last_new_job'].astype(str))
#train['city'] = le.fit_transform(train['city'].astype(str))



/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:55: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:57: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead


In [11]:
pp.ProfileReport(ds)


Summarize dataset:   0%|          | 0/26 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [10]:
ds['last_new_job'] = ds['last_new_job'].astype(int)

/home/ec2-user/anaconda3/envs/python3/lib/python3.6/site-packages/ipykernel/__main__.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  if __name__ == '__main__':


In [12]:
X_train, X_test = train_test_split(ds,test_size=0.3, train_size=0.7, random_state=5, shuffle=True)

In [13]:
bucket = 'sagemaker-angular-project-2021'
folder = 'hr2'

In [14]:
features_channel = folder + '/features'

In [15]:
s3 = boto3.client('s3')

In [16]:
X_train.to_csv('prep_train.csv',index = False,header = False)

In [17]:
X_test.to_csv('prep_test.csv',index = False,header = False)

In [18]:
train_channel = folder + '/train'

In [19]:
validation_channel = folder + '/validation'

In [20]:
sess = sagemaker.Session()

In [21]:


sess.upload_data(path = 'prep_train.csv',bucket = bucket, key_prefix = train_channel)

's3://sagemaker-angular-project-2021/hr2/train/prep_train.csv'

In [22]:
sess.upload_data(path = 'prep_test.csv',bucket = bucket, key_prefix = validation_channel)

's3://sagemaker-angular-project-2021/hr2/validation/prep_test.csv'

In [23]:
s3_train_data = 's3://{}/{}'.format(bucket,train_channel)

In [24]:
s3_test_data = 's3://{}/{}'.format(bucket,validation_channel)

In [25]:
s3_output_location = 's3://{}/{}'.format(bucket,folder)

In [26]:
s3_output_location

's3://sagemaker-angular-project-2021/hr2'

In [27]:
containers = {'us-west-2': '433757028032.dkr.ecr.us-west-2.amazonaws.com/xgboost:latest',
              'us-east-1': '811284229777.dkr.ecr.us-east-1.amazonaws.com/xgboost:latest',
              'us-east-2': '825641698319.dkr.ecr.us-east-2.amazonaws.com/xgboost:latest',
              'eu-west-1': '685385470294.dkr.ecr.eu-west-1.amazonaws.com/xgboost:latest'}
# containers were the algorithm resides

In [28]:
role = get_execution_role()

In [29]:
from sagemaker.xgboost.estimator import XGBoost

In [30]:
estimator = sagemaker.estimator.Estimator(containers[boto3.Session().region_name],
                                       role, 
                                       instance_count=1, 
                                       instance_type='ml.m4.xlarge',
                                       output_path=s3_output_location,
                                       sagemaker_session=sess,
                                       base_job_name ='xgboost-bbc-v7')


estimator.set_hyperparameters(max_depth=5,
                              objective="multi:softmax",
                              num_class=6,
                              num_round=50)


In [31]:
training_input_config = sagemaker.inputs.TrainingInput(s3_data=s3_train_data,content_type="csv")
validation_input_config = sagemaker.inputs.TrainingInput(s3_data=s3_test_data,content_type="csv")

In [ ]:
estimator.fit({'train':training_input_config, 'validation':validation_input_config})

2021-03-30 06:40:32 Starting - Starting the training job...
2021-03-30 06:40:57 Starting - Launching requested ML instancesProfilerReport-1617086432: InProgress
.........
2021-03-30 06:42:17 Starting - Preparing the instances for training......
2021-03-30 06:43:22 Downloading - Downloading input data...
2021-03-30 06:43:58 Training - Downloading the training image..

In [37]:
predictor = estimator.deploy(initial_instance_count = 1,
                            instance_type = "ml.t2.medium",
                            endpoint_name = "hrNew-xgboost-jce")

----------------!